In [289]:
import pandas as pd
pd.set_option("display.max_columns", None)
pd.set_option('display.max_rows', None)

In [62]:
usopen_2011_points = pd.read_csv("./data/2011-ausopen-points.csv")

In [63]:
usopen_2011_points.head()

match_id ElapsedTime  SetNo  P1GamesWon  P2GamesWon  SetWinner  \
0  2011-ausopen-1101    00:00:00    1.0         0.0         0.0          0   
1  2011-ausopen-1101     0:00:00    1.0         0.0         0.0          0   
2  2011-ausopen-1101     0:00:23    1.0         0.0         0.0          0   
3  2011-ausopen-1101     0:00:59    1.0         0.0         0.0          0   
4  2011-ausopen-1101     0:01:57    1.0         1.0         0.0          0   

   GameNo  GameWinner  PointNumber  PointWinner  PointServer  Speed_KMH  \
0     1.0           0            0          0.0          0.0        0.0   
1     1.0           0            1          1.0          2.0      166.0   
2     1.0           0            2          1.0          2.0      132.0   
3     1.0           0            3          1.0          2.0      144.0   
4     1.0           1            4          1.0          2.0      137.0   

   Rally P1Score P2Score  P1Momentum  P2Momentum  P1PointsWon  P2PointsWon  \
0    0.0       0       0           0           0          0.0          0.0   
1    4.0      15       0           1           1          1.0          0.0   
2    4.0      30       0           2           1          2.0          0.0   
3    8.0      40       0           3           1          3.0          0.0   
4    6.0       0       0           9           1          4.0          0.0   

   P1Ace  P2Ace  P1Winner  P2Winner  P1DoubleFault  P2DoubleFault  P1UnfErr  \
0    0.0    0.0       0.0       0.0            0.0            0.0       0.0   
1    0.0    0.0       0.0       0.0            0.0            0.0       0.0   
2    0.0    0.0       0.0       0.0            0.0            0.0       0.0   
3    0.0    0.0       0.0       0.0            0.0            0.0       0.0   
4    0.0    0.0       0.0       0.0            0.0            0.0       0.0   

   P2UnfErr  P1NetPoint  P2NetPoint  P1NetPointWon  P2NetPointWon  \
0       0.0           0           0              0              0   
1       1.0           0           0              0              0   
2       1.0           0           0              0              0   
3       1.0           0           0              0              0   
4       1.0           0           0              0              0   

   P1BreakPoint  P2BreakPoint  P1BreakPointWon  P2BreakPointWon  P1FirstSrvIn  \
0             0             0                0                0           0.0   
1             0             0                0                0           0.0   
2             0             0                0                0           0.0   
3             0             0                0                0           0.0   
4             1             0                1                0           0.0   

   P2FirstSrvIn  P1FirstSrvWon  P2FirstSrvWon  P1SecondSrvIn  P2SecondSrvIn  \
0           0.0            0.0            0.0            0.0            0.0   
1           1.0            0.0            0.0            0.0            0.0   
2           0.0            0.0            0.0            0.0            1.0   
3           0.0            0.0            0.0            0.0            1.0   
4           0.0            0.0            0.0            0.0            1.0   

   P1SecondSrvWon  P2SecondSrvWon  P1ForcedError  P2ForcedError  History  \
0             0.0             0.0            0.0            0.0      0.0   
1             0.0             0.0            0.0            0.0  21020.0   
2             0.0             0.0            0.0            0.0  22020.0   
3             0.0             0.0            0.0            0.0  22020.0   
4             0.0             0.0            0.0            0.0  21022.0   

   Speed_MPH  P1BreakPointMissed  P2BreakPointMissed  ServeIndicator  \
0        0.0                   0                   0               0   
1      103.0                   0                   0               2   
2       82.0                   0                   0               2   
3       89.0              

In [190]:
usopen_2011_matches = pd.read_csv("./data/2011-frenchopen-matches.csv")

In [191]:
usopen_2011_matches.head()

match_id  year        slam  match_num           player1  \
0  2011-frenchopen-1101  2011  frenchopen       1101      Rafael Nadal   
1  2011-frenchopen-1104  2011  frenchopen       1104  Denis Gremelmayr   
2  2011-frenchopen-1105  2011  frenchopen       1105       Sam Querrey   
3  2011-frenchopen-1106  2011  frenchopen       1106     Ivan Ljubicic   
4  2011-frenchopen-1108  2011  frenchopen       1108       Juan Monaco   

                 player2    status  winner event_name    round  \
0             John Isner  Complete       1   event_MS  round_1   
1      Nikolay Davydenko  Complete       2   event_MS  round_1   
2  Philipp Kohlschreiber  Complete       1   event_MS  round_1   
3       Somdev Devvarman  Complete       1   event_MS  round_1   
4      Fernando Verdasco  Complete       2   event_MS  round_1   

                court_name court_id player1id player2id nation1 nation2  
0  Court Philippe Chatrier        A   atpn409   atpi186     ESP     USA  
1                  Court 6        H   atpg512   atpd402     GER     RUS  
2                  Court 7        I   atpq927   atpk435     USA     GER  
3                  Court 3        E   atpl360   atpd616     CRO     IND  
4                  Court 2        D   atpma21   atpv306     ARG     ESP

In [61]:
# Just look at mens games
usopen_2011_matches = usopen_2011_matches[usopen_2011_matches["event_name"] == "event_MS"]

# player -> [serve_points_won, serve_points_attempted]
server_count = {}

# player -> [return_points_won, return_points_attempted]
returner_count = {}
point_number = 0
total_number_of_points = usopen_2011_points.shape[0]
for index, match in usopen_2011_matches.iterrows():
    player_1 = match["player1"]
    player_2 = match["player2"]
    match_id = match["match_id"]
    curr_match = usopen_2011_points.iloc[point_number]["match_id"]
    
    if player_1 not in server_count:
        server_count[player_1] = [0,0]
        returner_count[player_1] = [0,0]
    if player_2 not in server_count:
        server_count[player_2] = [0,0]
        returner_count[player_2] = [0,0]
    
    point_number += 1
    while point_number < total_number_of_points and match_id == usopen_2011_points.iloc[point_number]["match_id"]:
        point = usopen_2011_points.iloc[point_number]
        point_server = point["PointServer"]
        point_winner = point["PointWinner"]

        if point_server == 1 and point_winner == 1:
            server_count[player_1][0] += 1
            server_count[player_1][1] += 1
            returner_count[player_2][1] += 1
        elif point_server == 2 and point_winner == 2:
            server_count[player_2][0] += 1
            server_count[player_2][1] += 1
            returner_count[player_1][1] += 1
        elif point_server == 1 and point_winner == 2:
            server_count[player_1][1] += 1
            returner_count[player_2][0] += 1
            returner_count[player_2][1] += 1
        elif point_server == 2 and point_winner == 1:
            server_count[player_2][1] += 1
            returner_count[player_1][0] += 1
            returner_count[player_1][1] += 1
        
        point_number += 1
            
        
        
        

In [81]:
ausopen_matches_suffix = "-ausopen-matches.csv"
ausopen_points_suffix = "-ausopen-points.csv"

usopen_matches_suffix = "-usopen-matches.csv"
usopen_points_suffix = "-usopen-points.csv"

wimbledon_matches_suffix = "-wimbledon-matches.csv"
wimbledon_points_suffix = "-wimbledon-points.csv"

frenchopen_matches_suffix = "-frenchopen-matches.csv"
frenchopen_points_suffix = "-frenchopen-points.csv"

years = ["2011", "2012", "2013"]

In [211]:
def compute_serve_return_values(year, matches_suffix, points_suffix, server_count, returner_count):
    points = pd.read_csv("./data/" + year + points_suffix)
    matches = pd.read_csv("./data/" + year + matches_suffix)
    matches_mens = matches[(matches["event_name"] == "event_MS") | (matches["event_name"] == "Men's Singles")]
    
    point_number = 0
    total_number_of_points = points.shape[0]
    p1_serve_tally = []
    p2_serve_tally = []
    for index, match in matches_mens.iterrows():
        player_1 = match["player1"]
        player_2 = match["player2"]
        match_id = match["match_id"]
        
        if player_1 not in server_count:
            server_count[player_1] = [0,0]
            returner_count[player_1] = [0,0]
        if player_2 not in server_count:
            server_count[player_2] = [0,0]
            returner_count[player_2] = [0,0]
        
        point_number += 1
        points_p1_served = 0
        points_p2_served = 0
        while point_number < total_number_of_points and match_id == points.iloc[point_number]["match_id"]:
            point = points.iloc[point_number]
            if pd.isnull(point["PointServer"]) or pd.isnull(point["PointWinner"]):
                point_number += 1
                continue
            point_server = int(point["PointServer"])
            point_winner = int(point["PointWinner"])
            
            if point_server == 1:
                if point_winner == 1:
                    server_count[player_1][0] += 1
                    server_count[player_1][1] += 1
                    returner_count[player_2][1] += 1
                elif point_winner == 2:
                    server_count[player_1][1] += 1
                    returner_count[player_2][0] += 1
                    returner_count[player_2][1] += 1
                points_p1_served += 1
            
            if point_server == 2:
                if point_winner == 2:
                    server_count[player_2][0] += 1
                    server_count[player_2][1] += 1
                    returner_count[player_1][1] += 1
                elif point_winner == 1:
                    server_count[player_2][1] += 1
                    returner_count[player_1][0] += 1
                    returner_count[player_1][1] += 1
                points_p2_served += 1
        
            point_number += 1
        p1_serve_tally.append(points_p1_served)
        p2_serve_tally.append(points_p2_served)
    
    p1_served_column = pd.DataFrame(p1_serve_tally, columns=["points p1 served"])
    p2_served_column = pd.DataFrame(p2_serve_tally, columns=["points p2 served"])
    matches_mens["points p1 served"] = p1_served_column["points p1 served"]
    matches_mens["points p2 served"] = p2_served_column["points p2 served"]
    return matches_mens
        

In [212]:
server_count = {}
returner_count = {}
mens_matches = {}

for year in years:
    matches_aus = compute_serve_return_values(year, ausopen_matches_suffix, ausopen_points_suffix, server_count, returner_count)
    matches_fr = compute_serve_return_values(year, frenchopen_matches_suffix, frenchopen_points_suffix, server_count, returner_count)
    matches_w = compute_serve_return_values(year, wimbledon_matches_suffix, wimbledon_points_suffix, server_count, returner_count)
    matches_us = compute_serve_return_values(year, usopen_matches_suffix, usopen_points_suffix, server_count, returner_count)
    
    mens_matches[year + ausopen_matches_suffix] = matches_aus
    mens_matches[year + frenchopen_matches_suffix] = matches_fr
    mens_matches[year + wimbledon_matches_suffix] = matches_w
    mens_matches[year + usopen_matches_suffix] = matches_us
    
    
    
    

/Users/VillasBoas/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:61: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/Users/VillasBoas/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:62: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [290]:
matches = pd.read_csv("./data/2011-frenchopen-matches.csv")
matches_mens = matches[(matches["event_name"] == "event_MS") | (matches["event_name"] == "Men's Singles")]

matches_mens.head(100)

match_id  year        slam  match_num                 player1  \
0   2011-frenchopen-1101  2011  frenchopen       1101            Rafael Nadal   
1   2011-frenchopen-1104  2011  frenchopen       1104        Denis Gremelmayr   
2   2011-frenchopen-1105  2011  frenchopen       1105             Sam Querrey   
3   2011-frenchopen-1106  2011  frenchopen       1106           Ivan Ljubicic   
4   2011-frenchopen-1108  2011  frenchopen       1108             Juan Monaco   
5   2011-frenchopen-1109  2011  frenchopen       1109              Mardy Fish   
6   2011-frenchopen-1111  2011  frenchopen       1111           Jeremy Chardy   
7   2011-frenchopen-1112  2011  frenchopen       1112         Michael Russell   
8   2011-frenchopen-1113  2011  frenchopen       1113        Marcos Baghdatis   
9   2011-frenchopen-1116  2011  frenchopen       1116           Ryan Harrison   
10  2011-frenchopen-1117  2011  frenchopen       1117             Andy Murray   
11  2011-frenchopen-1119  2011  frenchopen       1119          Arnaud Clement   
12  2011-frenchopen-1121  2011  frenchopen       1121     Alexandr Dolgopolov   
13  2011-frenchopen-1124  2011  frenchopen       1124          Julian Reister   
14  2011-frenchopen-1125  2011  frenchopen       1125         Nicolas Almagro   
15  2011-frenchopen-1129  2011  frenchopen       1129          Kevin Anderson   
16  2011-frenchopen-1131  2011  frenchopen       1131  Edouard Roger-Vasselin   
17  2011-frenchopen-1132  2011  frenchopen       1132            Andreas Beck   
18  2011-frenchopen-1133  2011  frenchopen       1133            David Ferrer   
19  2011-frenchopen-1134  2011  frenchopen       1134        Julien Benneteau   
20  2011-frenchopen-1135  2011  frenchopen       1135           Kei Nishikori   
21  2011-frenchopen-1136  2011  frenchopen       1136              David Guez   
22  2011-frenchopen-1137  2011  frenchopen       1137          Michael Llodra   
23  2011-frenchopen-1139  2011  frenchopen       1139        Adrian Mannarino   
24  2011-frenchopen-1140  2011  frenchopen       1140              Bjorn Phau   
25  2011-frenchopen-1141  2011  frenchopen       1141      Stanislas Wawrinka   
26  2011-frenchopen-1143  2011  frenchopen       1143           Florent Serra   
27  2011-frenchopen-1144  2011  frenchopen       1144               Jan Hajek   
28  2011-frenchopen-1147  2011  frenchopen       1147          Vincent Millot   
29  2011-frenchopen-1148  2011  frenchopen       1148         Feliciano Lopez   
30  2011-frenchopen-1149  2011  frenchopen       1149           Tomas Berdych   
31  2011-frenchopen-1150  2011  frenchopen       1150           Fabio Fognini   
32  2011-frenchopen-1152  2011  frenchopen       1152         Robert Kendrick   
33  2011-frenchopen-1153  2011  frenchopen       1153             Marin Cilic   
34  2011-frenchopen-1154  2011  frenchopen       1154            Marc Gicquel   
35  2011-frenchopen-1156  2011  frenchopen       1156                Go Soeda   
36  2011-frenchopen-1157  2011  frenchopen       1157         Richard Gasquet   
37  2011-frenchopen-1159  2011  frenchopen       1159     Teymuraz Gabashvili   
38  2011-frenchopen-1161  2011  frenchopen       1161   Juan Martin Del Potro   
39  2011-frenchopen-1162  2011  frenchopen       1162          Ernests Gulbis   
40  2011-frenchopen-1163  2011  frenchopen       1163            Benoit Paire   
41  2011-frenchopen-1164  2011  frenchopen       1164        Thiemo De Bakker   
42  2011-frenchopen-1201  2011  frenchopen       1201            Rafael Nadal   
43  2011-frenchopen-1202  2011  frenchopen       1202            Antonio Veic   
44  2011-frenchopen-1203  2011  frenchopen       1203             Sam Querrey   
45  2011-frenchopen-1204  2011  frenchopen       1204          Xavier Malisse   
46  2011-frenchopen-1205  2011  frenchopen       1205              Mardy Fish   
47  2011-frenchopen-1206  2011  frenchopen       1206           Jeremy Chardy   
48  2011-frenchopen-1207  2011  frenchopen     

In [168]:
players = list(returner_count.keys())
players

['Rafael Nadal',
 'Marcos Daniel',
 'Bernard Tomic',
 'Jeremy Chardy',
 'John Isner',
 'Florent Serra',
 'Donald Young',
 'Marin Cilic',
 'Juan Ignacio Chela',
 'Michael Llodra',
 'David Nalbandian',
 'Lleyton Hewitt',
 'Richard Berankis',
 'Marinko Matosevic',
 'Michael Russell',
 'Matthew Ebden',
 'Jarkko Nieminen',
 'David Ferrer',
 'Robin Soderling',
 'Potito Starace',
 'Philipp Petzschner',
 'Jo-Wilfried Tsonga',
 'Carsten Ball',
 'Pere Riba',
 'Dudi Sela',
 'Juan Martin Del Potro',
 'Grega Zemlja',
 'Marcos Baghdatis',
 'Karol Beck',
 'Andy Murray',
 'Tomas Berdych',
 'Marco Crugnola',
 'Frank Dancevic',
 'Richard Gasquet',
 'Fabio Fognini',
 'Kei Nishikori',
 'Rainer Schuettler',
 'Fernando Verdasco',
 'Peter Luczak',
 'Ivan Ljubicic',
 'Marcel Granollers',
 'Novak Djokovic',
 'Andy Roddick',
 'Jan Hajek',
 'Simon Greul',
 'Juan Monaco',
 'Stanislas Wawrinka',
 'Teymuraz Gabashvili',
 'Thiemo de Bakker',
 'Gael Monfils',
 'Mardy Fish',
 'Victor Hanescu',
 'Lukasz Kubot',
 'Sam Q

Define:

f_i_opp := $\frac{1}{total\ points\ i\ returned}\sum_{j \in opp(i)} \frac{points\ won\ on\ serve\ by j}{total\ points\ served\ by\ j} * (points\ i\ returned\ on\ j)$

g_i_opp := $\frac{1}{total\ points\ i\ served}\sum_{j \in opp(i)} \frac{points\ won\ on\ return\ by j}{total\ points\ returned\ by\ j} * (points\ i\ served\ on\ j)$

In [245]:
def compute_serve_return_opp_values(mens_matches, server_count, returner_count, server_opp_count, returner_opp_count):
    for tournament in mens_matches:
        for index, match in mens_matches[tournament].iterrows():
            player_1 = match["player1"]
            player_2 = match["player2"]
        
            if player_1 not in server_opp_count:
                server_opp_count[player_1] = 0
                returner_opp_count[player_1] = 0
            if player_2 not in server_opp_count:
                server_opp_count[player_2] = 0
                returner_opp_count[player_2] = 0
            
            
            server_opp_count[player_1] += (server_count[player_2][0] / server_count[player_2][1]) * match["points p2 served"]
            server_opp_count[player_2] += (server_count[player_1][0] / server_count[player_1][1]) * match["points p1 served"]
        
            returner_opp_count[player_1] += (returner_count[player_2][0] / returner_count[player_2][1]) * match["points p1 served"]
            returner_opp_count[player_2] += (returner_count[player_1][0] / returner_count[player_1][1]) * match["points p2 served"]
            
    for player in players:
        server_opp_count[player] = server_opp_count[player] / returner_count[player][1]
        returner_opp_count[player] = returner_opp_count[player] / server_count[player][1]
        


In [246]:
server_opp_count = {}
returner_opp_count = {}
compute_serve_return_opp_values(mens_matches, server_count, returner_count, server_opp_count, returner_opp_count)

In [248]:
returner_opp_count

{'Rafael Nadal': 0.3756533680584795,
 'Marcos Daniel': 0.4386245501799281,
 'Bernard Tomic': 0.37615393469503783,
 'Jeremy Chardy': 0.366399271183749,
 'John Isner': 0.3557751786360574,
 'Florent Serra': 0.3202811986863711,
 'Donald Young': 0.3726824121055096,
 'Marin Cilic': 0.36488803679278475,
 'Juan Ignacio Chela': 0.3894518197010769,
 'Michael Llodra': 0.36058518030325293,
 'David Nalbandian': 0.3699947169580649,
 'Lleyton Hewitt': 0.38516361589651754,
 'Richard Berankis': 0.38353913275640755,
 'Marinko Matosevic': 0.43577989566631875,
 'Michael Russell': 0.3932654902886329,
 'Matthew Ebden': 0.34963325183374083,
 'Jarkko Nieminen': 0.40318201066504894,
 'David Ferrer': 0.36476395915990123,
 'Robin Soderling': 0.3448390281631297,
 'Potito Starace': 0.38656838656838655,
 'Philipp Petzschner': 0.3676428721653599,
 'Jo-Wilfried Tsonga': 0.3663692233390237,
 'Carsten Ball': 0.3106060606060606,
 'Pere Riba': 0.37658128170280986,
 'Dudi Sela': 0.3965213471163903,
 'Juan Martin Del Potro

In [249]:
relative_serve_ability = {}
relative_return_ability = {}
for player in players:
    raw_serve_ability = float(server_count[player][0]) / server_count[player][1]
    opp_return_ability = returner_opp_count[player]
    relative_serve_ability[player] = raw_serve_ability - (1 - opp_return_ability)
    
    raw_return_ability = float(returner_count[player][0]) / returner_count[player][1]
    opp_serve_ability = server_opp_count[player]
    relative_return_ability[player] = raw_return_ability - (1 - opp_serve_ability)

In [265]:
print(returner_count["Ruben Ramirez Hidalgo"])
print(1 - server_opp_count["Ruben Ramirez Hidalgo"])

[49, 112]
0.3375661375661375


In [258]:
relative_serve_ability

{'Rafael Nadal': 0.0411924801092195,
 'Marcos Daniel': -0.484452372896995,
 'Bernard Tomic': 0.015633840132389998,
 'Jeremy Chardy': -0.03533483286249384,
 'John Isner': 0.06846472372783718,
 'Florent Serra': -0.10906662740058537,
 'Donald Young': -0.03715365346826083,
 'Marin Cilic': 0.027321899226647184,
 'Juan Ignacio Chela': -0.05464266848789945,
 'Michael Llodra': 0.01893450851822409,
 'David Nalbandian': -0.026892442575009112,
 'Lleyton Hewitt': 0.03246652046083287,
 'Richard Berankis': -0.025551776334501564,
 'Marinko Matosevic': -0.03591821754122837,
 'Michael Russell': -0.058201778334391885,
 'Matthew Ebden': -0.08645697373016892,
 'Jarkko Nieminen': -0.021988057362161917,
 'David Ferrer': 0.04180913620507831,
 'Robin Soderling': 0.0014948723189738278,
 'Potito Starace': -0.06343161343161341,
 'Philipp Petzschner': -0.011352561624594415,
 'Jo-Wilfried Tsonga': 0.03339508540798919,
 'Carsten Ball': -0.02022100706311236,
 'Pere Riba': -0.07107214790007832,
 'Dudi Sela': 0.007299

In [261]:
max(relative_return_ability, key=relative_return_ability.get)

'Ruben Ramirez Hidalgo'

In [185]:
returner_count['Maxime Teixeira']

[98, 235]

In [186]:
server_opp_count['Maxime Teixeira']

[1683, 2431]

## Trying to analyze the 2011-2015 every game dataset

In [483]:
big.iloc[200]["date"]

Timestamp('2011-09-08 00:00:00')

In [512]:
from datetime import datetime
big = pd.read_csv("./data/2011-2015_matches.csv")
big["date"] = big["date"].apply(lambda x: datetime.strptime(x, '%d %b %y'))

In [485]:
games_before_2014 = big[big["date"] < datetime.strptime("01 Jan 14", '%d %b %y')]

In [513]:
# Clean games_before_2014
for index, match in big.iterrows():
    player_1 = match["server1"]
    player_2 = match["server2"]
    
    player_1_bad = (len(player_1.split()) <= 1) or (player_1.find("/") != -1)
    player_2_bad = (len(player_2.split()) <= 1) or (player_2.find("/") != -1)
    if player_1_bad or player_2_bad:
        games_before_2014.drop(index, inplace=True)

games_before_2014.reset_index(inplace=True, drop=True)

In [524]:
test = {}
for index, match in big.iterrows():
    tourn = match["tny_name"]
    abbrev = tourn[0:6]
    if abbrev not in test:
        test[abbrev] = set()
    test[abbrev].add(tourn)
arr = []
for el in test:
    if len(test[el]) > 2:
        arr.append(test[el])

In [530]:
test

{'ATPStu': {'ATPStudenaCroatiaOpen-ATPUmag2011'},
 'Credit': {'CreditAgricoleSuisseOpenGstaad-ATPGstaad',
  'CreditAgricoleSuisseOpenGstaad-ATPGstaad2011'},
 'Farmer': {'FarmersClassic-ATPLosAngeles',
  'FarmersClassic-ATPLosAngeles.html',
  'FarmersClassic-ATPLosAngeles2011'},
 'ATPKit': {'ATPKitzbuhel-AustrianOpen',
  'ATPKitzbuhel2011',
  'ATPKitzbuhel2011.html'},
 'LeggMa': {'LeggMasonTennisClassic-ATPWashington2011',
  'LeggMasonTennisClassic-ATPWashington2011.html'},
 'Rogers': {'RogersCup-ATPMontreal',
  'RogersCup-ATPMontreal.html',
  'RogersCup-ATPMontreal2011',
  'RogersCup-ATPMontreal2011.html',
  'RogersCup-ATPToronto',
  'RogersCup-ATPToronto.html'},
 'Wester': {'Western&amp;SouthernOpen-ATPCincinnati',
  'Western&amp;SouthernOpen-ATPCincinnati.html',
  'Western&amp;SouthernOpen-ATPCincinnati2011',
  'Western&amp;SouthernOpen-ATPCincinnati2011.html'},
 'Winsto': {'Winston-SalemOpen-ATPWinston-Salem',
  'WinstonSalemOpen-ATPWinstonSalem',
  'WinstonSalemOpen-ATPWinstonSalem

In [486]:
# Clean games_before_2014
for index, match in games_before_2014.iterrows():
    player_1 = match["server1"]
    player_2 = match["server2"]
    
    player_1_bad = (len(player_1.split()) <= 1) or (player_1.find("/") != -1)
    player_2_bad = (len(player_2.split()) <= 1) or (player_2.find("/") != -1)
    if player_1_bad or player_2_bad:
        games_before_2014.drop(index, inplace=True)

games_before_2014.reset_index(inplace=True, drop=True)

/Users/VillasBoas/anaconda3/lib/python3.6/site-packages/pandas/core/frame.py:4174: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [487]:
big_server_count = {}
big_returner_count = {}
p1_serve_tally = []
p2_serve_tally = []
for index, match in games_before_2014.iterrows():
    player_1 = match["server1"]
    player_2 = match["server2"]
    
    if player_1 not in big_server_count:
        big_server_count[player_1] = [0,0]
        big_returner_count[player_1] = [0,0]
    if player_2 not in big_server_count:
        big_server_count[player_2] = [0,0]
        big_returner_count[player_2] = [0,0]
    
    points = match["pbp"]
    p = 0
    server = 1
    points_p1_served = 0
    points_p2_served = 0
    while p < len(points):
        if points[p] == "S" or points[p] == "R" or points[p] == "A" or points[p] == "D":
            if server == 1:
                if points[p] == "S" or points[p] == "A":
                    big_server_count[player_1][0] += 1
                    big_server_count[player_1][1] += 1
                    big_returner_count[player_2][1] += 1
                elif points[p] == "R" or points[p] == "D":
                    big_server_count[player_1][1] += 1
                    big_returner_count[player_2][0] += 1
                    big_returner_count[player_2][1] += 1
                points_p1_served += 1
            
            if server == -1:
                if points[p] == "S" or points[p] == "A":
                    big_server_count[player_2][0] += 1
                    big_server_count[player_2][1] += 1
                    big_returner_count[player_1][1] += 1
                elif points[p] == "R" or points[p] == "D":
                    big_server_count[player_2][1] += 1
                    big_returner_count[player_1][0] += 1
                    big_returner_count[player_1][1] += 1
                points_p2_served += 1
        elif points[p] == ";" or points[p] == ".":
            # End of game, end of set, respectively
            server *= -1
        elif points[p] == "/":
            # Handle tiebreak
            next_set_server = server * -1
            server *= -1
            while p < len(points) and points[p] != ".":
                if points[p] == "/":
                    server *= -1
                elif points[p] == "S" or points[p] == "R" or points[p] == "A" or points[p] == "D":
                    if server == 1:
                        if points[p] == "S" or points[p] == "A":
                            big_server_count[player_1][0] += 1
                            big_server_count[player_1][1] += 1
                            big_returner_count[player_2][1] += 1
                        elif points[p] == "R" or points[p] == "D":
                            big_server_count[player_1][1] += 1
                            big_returner_count[player_2][0] += 1
                            big_returner_count[player_2][1] += 1
                        points_p1_served += 1
            
                    elif server == -1:
                        if points[p] == "S" or points[p] == "A":
                            big_server_count[player_2][0] += 1
                            big_server_count[player_2][1] += 1
                            big_returner_count[player_1][1] += 1
                        elif points[p] == "R" or points[p] == "D":
                            big_server_count[player_2][1] += 1
                            big_returner_count[player_1][0] += 1
                            big_returner_count[player_1][1] += 1
                        points_p2_served += 1
                p += 1
            server = next_set_server
        p += 1
    if index == 5917:
        print(points_p1_served)
        print(points_p2_served)
    p1_serve_tally.append(points_p1_served)
    p2_serve_tally.append(points_p2_served)

p1_served_column = pd.DataFrame(p1_serve_tally, columns=["points p1 served"])
p2_served_column = pd.DataFrame(p2_serve_tally, columns=["points p2 served"])
games_before_2014["points p1 served"] = p1_served_column["points p1 served"]
games_before_2014["points p2 served"] = p2_served_column["points p2 served"]

/Users/VillasBoas/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:87: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/Users/VillasBoas/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:88: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [488]:
big_server_count

{'Olivier Rochus': [1578, 2674],
 'Fabio Fognini': [5455, 9189],
 'Robin Haase': [4736, 7531],
 'Marin Cilic': [5882, 9052],
 'Andreas Seppi': [5616, 8931],
 'Alexandr Dolgopolov': [4972, 7772],
 'Albert Ramos': [4460, 7254],
 'Carlos Berlocq': [4093, 6657],
 'Juan Carlos Ferrero': [1226, 2000],
 'Matthias Bachinger': [1603, 2574],
 'Julien Benneteau': [4928, 7787],
 'Stanislas Wawrinka': [6545, 9951],
 'Peter Luczak': [132, 200],
 'Frederico Gil': [939, 1568],
 'Fernando Verdasco': [5597, 8647],
 'Jarkko Nieminen': [5022, 8174],
 'Nicolas Almagro': [6929, 10303],
 'Andreas Haider-Maurer': [911, 1550],
 'Mikhail Youzhny': [6222, 9814],
 'Marcel Granollers': [4090, 6618],
 'Feliciano Lopez': [5161, 7857],
 'Alex Bogomolov Jr': [876, 1524],
 'Grigor Dimitrov': [5558, 8461],
 'Igor Kunitsyn': [1404, 2424],
 'Ryan Sweeting': [723, 1180],
 'Alejandro Falla': [2959, 4919],
 'Thomaz Bellucci': [3473, 5592],
 'Gilles Muller': [3157, 4742],
 'Mardy Fish': [2882, 4422],
 'Yen-Hsun Lu': [2940, 46

In [489]:
games_before_2014

index   pbp_id       date  \
0         0  2231275 2011-07-28   
1         1  2231276 2011-07-28   
2         2  2236280 2011-07-29   
3         3  2233792 2011-07-29   
4         4  2233791 2011-07-29   
5         5  2229262 2011-07-28   
6         6  2228887 2011-07-28   
7         7  2229260 2011-07-28   
8         8  2229257 2011-07-29   
9         9  2234483 2011-07-29   
10       10  2234484 2011-07-29   
11       11  2234481 2011-07-29   
12       12  2234478 2011-07-29   
13       13  2231345 2011-07-28   
14       14  2231340 2011-07-28   
15       15  2231342 2011-07-28   
16       16  2231339 2011-07-29   
17       17  2233789 2011-07-29   
18       18  2242876 2011-07-31   
19       19  2239568 2011-08-01   
20       20  2239566 2011-08-01   
21       21  2239565 2011-08-01   
22       22  2239561 2011-08-01   
23       23  2239563 2011-08-01   
24       24  2239564 2011-08-01   
25       25  2239567 2011-08-01   
26       26  2244797 2011-08-02   
27       27  2239562 2011-08-02   
28       28  2244795 2011-08-02   
29       29  2244796 2011-08-02   
30       30  2245392 2011-08-03   
31       31  2244798 2011-08-04   
32       32  2249989 2011-08-04   
33       33  2249983 2011-08-04   
34       34  2239568 2011-08-01   
35       35  2244796 2011-08-02   
36       36  2237435 2011-07-30   
37       37  2237440 2011-07-30   
38       38  2239534 2011-07-31   
39       39  2237432 2011-07-30   
40       40  2237428 2011-07-30   
41       41  2241982 2011-07-31   
42       42  2236355 2011-07-30   
43       43  2236356 2011-07-30   
44       44  2239367 2011-07-30   
45       45  2240303 2011-07-30   
46       46  2239368 2011-07-31   
47       47  2239540 2011-07-31   
48       48  2243087 2011-07-31   
49       49  2243088 2011-07-31   
50       50  2243089 2011-07-31   
51       51  2239503 2011-08-01   
52       52  2239504 2011-08-01   
53       53  2244637 2011-08-01   
54       54  2244638 2011-08-01   
55       55  2239505 2011-08-02   
56       56  2239502 2011-08-02   
57       57  2239495 2011-08-02   
58       58  2239498 2011-08-02   
59       59  2244641 2011-08-02   
60       60  2247730 2011-08-02   
61       61  2247016 2011-08-03   
62       62  2247017 2011-08-03   
63       63  2244642 2011-08-03   
64       64  2251928 2011-08-04   
65       65  2239498 2011-08-02   
66       66  2244641 2011-08-02   
67       67  2254478 2011-08-05   
68       68  2258240 2011-08-06   
69       69  2260018 2011-08-07   
70       70  2260019 2011-08-07   
71       71  2260020 2011-08-07   
72       72  2260021 2011-08-07   
73       73  2260022 2011-08-07   
74       74  2260024 2011-08-07   
75       75  2257497 2011-08-08   
76       76  2257498 2011-08-08   
77       77  2257499 2011-08-08   
78       78  2257500 2011-08-08   
79       79  2257492 2011-08-08   
80       80  2257495 2011-08-08   
81       81  2262282 2011-08-08   
82       82  2257487 2011-08-08   
83       83  2257490 2011-08-09   
84       84  2257491 2011-08-09   
85       85  2262284 2011-08-09   
86       86  2257489 2011-08-09   
87       87  2264476 2011-08-09   
88       88  2262287 2011-08-09   
89       89  2268324 2011-08-10   
90       90  2265182 2011-08-10   
91       91  2265183 2011-08-10   
92       92  2267285 2011-08-10   
93       93  2257499 2011-08-08   
94       94  2257487 2011-08-08   
95       95  2257490 2011-08-09   
96       96  2257491 2011-08-09   
97       97  2264478 2011-08-10   
98       98  2268294 2011-08-11   
99       99  2269981 2011-08-12   
100     100  2269975 2011-08-13   
101     101  2272466 2011-08-13   
102     102  2275472 2011-08-14   
103     103  2276304 2011-08-13   
104     104  2276264 2011-08-15   
105     105  2276274 2011-08-15   
106     106  2276261 2011-08-15   
107     107  2280045 2011-08-15   
108     108  2276272 2011-08-15   
109     109  2280047 2011-08-15   
110     110  2276258 2011-08-16   
111     111  2276260 2011-08-16   
112     112  2276270 2011-08-16   
113     113  227

In [490]:
games_before_2014.iloc[14]["pbp"]

'RRRSR;RSSSRRRR;SSSS;SSRSS;SRSSS;RSSSRS;SRSRSRSRSRSS;RRSSSS;RSRSSS;RRSRSSSS;SRSSS;SRSSS;R/RR/SR/RS/SS/SR.RSRRSR;RRRR;SRSSS;SRSSRS;RSSSS;SSRSS;SSRSS;SSSRRS;RRSSRSRR;SSRRRR;SRRSRSRR;SRRSRR;R/RS/SS/SR/RS/SS/SR/S'

Define:

f_i_opp := $\frac{1}{total\ points\ i\ returned}\sum_{j \in opp(i)} \frac{points\ won\ on\ serve\ by j}{total\ points\ served\ by\ j} * (points\ i\ returned\ on\ j)$

g_i_opp := $\frac{1}{total\ points\ i\ served}\sum_{j \in opp(i)} \frac{points\ won\ on\ return\ by j}{total\ points\ returned\ by\ j} * (points\ i\ served\ on\ j)$

In [491]:
def compute_serve_return_opp_values(games_before_2014, big_server_count, big_returner_count, big_server_opp_count, big_returner_opp_count):
    for index, match in games_before_2014.iterrows():
        player_1 = match["server1"]
        player_2 = match["server2"]
    
        if player_1 not in big_server_opp_count:
            big_server_opp_count[player_1] = 0
            big_returner_opp_count[player_1] = 0
        if player_2 not in big_server_opp_count:
            big_server_opp_count[player_2] = 0
            big_returner_opp_count[player_2] = 0
            
            
        big_server_opp_count[player_1] += (big_server_count[player_2][0] / big_server_count[player_2][1]) * match["points p2 served"]
        big_server_opp_count[player_2] += (big_server_count[player_1][0] / big_server_count[player_1][1]) * match["points p1 served"]
        
        big_returner_opp_count[player_1] += (big_returner_count[player_2][0] / big_returner_count[player_2][1]) * match["points p1 served"]
        big_returner_opp_count[player_2] += (big_returner_count[player_1][0] / big_returner_count[player_1][1]) * match["points p2 served"]
            
    for player in players_big:
        big_server_opp_count[player] = big_server_opp_count[player] / big_returner_count[player][1]
        big_returner_opp_count[player] = big_returner_opp_count[player] / big_server_count[player][1]

In [492]:
players_big = list(big_returner_count.keys())
big_server_opp_count = {}
big_returner_opp_count = {}
compute_serve_return_opp_values(games_before_2014, big_server_count, big_returner_count, big_server_opp_count, big_returner_opp_count)

In [493]:
big_returner_opp_count

{'Olivier Rochus': 0.3732988021051067,
 'Fabio Fognini': 0.37056493255191236,
 'Robin Haase': 0.364416256599544,
 'Marin Cilic': 0.3684251491624491,
 'Andreas Seppi': 0.3686849687043739,
 'Alexandr Dolgopolov': 0.37687041640660585,
 'Albert Ramos': 0.36763475757742653,
 'Carlos Berlocq': 0.36610678622395115,
 'Juan Carlos Ferrero': 0.36910045697306,
 'Matthias Bachinger': 0.36059526484630067,
 'Julien Benneteau': 0.3687866139997437,
 'Stanislas Wawrinka': 0.3761632134409088,
 'Peter Luczak': 0.3476702485969044,
 'Frederico Gil': 0.3655389816045635,
 'Fernando Verdasco': 0.36959052746675897,
 'Jarkko Nieminen': 0.3681604703054141,
 'Nicolas Almagro': 0.3724484993637148,
 'Andreas Haider-Maurer': 0.36960391022449746,
 'Mikhail Youzhny': 0.3686775671136208,
 'Marcel Granollers': 0.3743065676877136,
 'Feliciano Lopez': 0.36671616452834255,
 'Alex Bogomolov Jr': 0.3661232156362666,
 'Grigor Dimitrov': 0.37543697128559217,
 'Igor Kunitsyn': 0.3606229935585528,
 'Ryan Sweeting': 0.36243599840

In [494]:
big_returner_count

{'Olivier Rochus': [904, 2621],
 'Fabio Fognini': [3530, 8900],
 'Robin Haase': [2706, 7345],
 'Marin Cilic': [3562, 9312],
 'Andreas Seppi': [3495, 9233],
 'Alexandr Dolgopolov': [2823, 7936],
 'Albert Ramos': [2676, 7120],
 'Carlos Berlocq': [2734, 6947],
 'Juan Carlos Ferrero': [814, 2189],
 'Matthias Bachinger': [923, 2584],
 'Julien Benneteau': [3038, 8057],
 'Stanislas Wawrinka': [3852, 10105],
 'Peter Luczak': [59, 212],
 'Frederico Gil': [573, 1517],
 'Fernando Verdasco': [3411, 9081],
 'Jarkko Nieminen': [2858, 7810],
 'Nicolas Almagro': [3984, 10716],
 'Andreas Haider-Maurer': [458, 1405],
 'Mikhail Youzhny': [3728, 9654],
 'Marcel Granollers': [2529, 6814],
 'Feliciano Lopez': [2578, 7717],
 'Alex Bogomolov Jr': [561, 1471],
 'Grigor Dimitrov': [3137, 8609],
 'Igor Kunitsyn': [834, 2357],
 'Ryan Sweeting': [373, 1098],
 'Alejandro Falla': [1796, 4901],
 'Thomaz Bellucci': [2104, 5656],
 'Gilles Muller': [1362, 4513],
 'Mardy Fish': [1829, 4560],
 'Yen-Hsun Lu': [1820, 4799],

In [495]:
len(list(big_returner_opp_count.keys()))

732

In [496]:
games_before_2014[games_before_2014["server2"] == "Carlos Gomez-Herrera"]

index   pbp_id       date                                   tny_name  \
3960   3976  4113257 2013-02-23  DubaiDutyFreeTennisChampionships-ATPDubai   

     tour  draw                server1               server2  winner  \
3960  ATP  Main  Andreas Haider-Maurer  Carlos Gomez-Herrera       2   

                                                    pbp    score  adf_flag  \
3960  SSSS;RRRR;SSSS;SSSS;RRRR;SSSS;RRRR;SSSS;RRRR.R...  6-3 6-3         1   

      wh_minutes  points p1 served  points p2 served  
3960          20                44                39

In [497]:
big_relative_serve_ability = {}
big_relative_return_ability = {}
for player in players_big:
    raw_serve_ability = float(big_server_count[player][0]) / big_server_count[player][1]
    opp_return_ability = big_returner_opp_count[player]
    big_relative_serve_ability[player] = raw_serve_ability - (1 - opp_return_ability)
    
    raw_return_ability = float(big_returner_count[player][0]) / big_returner_count[player][1]
    opp_serve_ability = big_server_opp_count[player]
    big_relative_return_ability[player] = raw_return_ability - (1 - opp_serve_ability)

In [498]:
big_relative_serve_ability

{'Olivier Rochus': -0.036574047558318945,
 'Fabio Fognini': -0.035790492412719255,
 'Robin Haase': -0.006716395106736717,
 'Marin Cilic': 0.01822629807981535,
 'Andreas Seppi': -0.002494070596936182,
 'Alexandr Dolgopolov': 0.016602789026266218,
 'Albert Ramos': -0.017532046944216617,
 'Carlos Berlocq': -0.019051693571752626,
 'Juan Carlos Ferrero': -0.017899543026939968,
 'Matthias Bachinger': -0.01663861238757658,
 'Julien Benneteau': 0.0016362351632213112,
 'Stanislas Wawrinka': 0.03388605536634337,
 'Peter Luczak': 0.00767024859690435,
 'Frederico Gil': -0.03560897757910997,
 'Fernando Verdasco': 0.016867039551875296,
 'Jarkko Nieminen': -0.017452448706085755,
 'Nicolas Almagro': 0.044971065606556726,
 'Andreas Haider-Maurer': -0.04265415429163155,
 'Mikhail Youzhny': 0.0026698230744931495,
 'Marcel Granollers': -0.007681948480313117,
 'Feliciano Lopez': 0.023582653009951327,
 'Alex Bogomolov Jr': -0.05907363475743421,
 'Grigor Dimitrov': 0.03233331923500715,
 'Igor Kunitsyn': -0.0

In [449]:
max(big_relative_serve_ability, key=big_relative_serve_ability.get)

'Roberto Bautista Agut'

In [462]:
big_server_count['Carlos Gomez-Herrera']

[28, 39]

In [451]:
big_relative_serve_ability['Carlos Gomez-Herrera']

0.043927365635550664

## Try to predict 2014 Matches

In [499]:
big = pd.read_csv("./data/2011-2015_matches.csv")
big["date"] = big["date"].apply(lambda x: datetime.strptime(x, '%d %b %y'))
games_2014_to_2015 = big[(big["date"] >= datetime.strptime("01 Jan 14", '%d %b %y')) & (big["date"] < datetime.strptime("01 Jan 15", '%d %b %y'))]
games_2014_to_2015

pbp_id       date                                        tny_name tour  \
5875  5435217 2014-01-01                AircelChennaiOpen-ATPChennai2014  ATP   
5876  5435209 2014-01-01                AircelChennaiOpen-ATPChennai2014  ATP   
5877  5435213 2014-01-02                AircelChennaiOpen-ATPChennai2014  ATP   
5878  5435215 2014-01-02                AircelChennaiOpen-ATPChennai2014  ATP   
5879  5442453 2014-01-03                AircelChennaiOpen-ATPChennai2014  ATP   
5880  5442452 2014-01-03                AircelChennaiOpen-ATPChennai2014  ATP   
5881  5442459 2014-01-03                AircelChennaiOpen-ATPChennai2014  ATP   
5882  5442457 2014-01-03                AircelChennaiOpen-ATPChennai2014  ATP   
5883  5447618 2014-01-04                AircelChennaiOpen-ATPChennai2014  ATP   
5884  5450733 2014-01-05                AircelChennaiOpen-ATPChennai2014  ATP   
5885  5450990 2014-01-06           ApiaInternationalSydney-ATPSydney2014  ATP   
5886  5450989 2014-01-06           ApiaInternationalSydney-ATPSydney2014  ATP   
5887  5450991 2014-01-06           ApiaInternationalSydney-ATPSydney2014  ATP   
5888  5458599 2014-01-07           ApiaInternationalSydney-ATPSydney2014  ATP   
5889  5458600 2014-01-07           ApiaInternationalSydney-ATPSydney2014  ATP   
5890  5458601 2014-01-07           ApiaInternationalSydney-ATPSydney2014  ATP   
5891  5450987 2014-01-07           ApiaInternationalSydney-ATPSydney2014  ATP   
5892  5458602 2014-01-07           ApiaInternationalSydney-ATPSydney2014  ATP   
5893  5450992 2014-01-07           ApiaInternationalSydney-ATPSydney2014  ATP   
5894  5450993 2014-01-07           ApiaInternationalSydney-ATPSydney2014  ATP   
5895  5462450 2014-01-08           ApiaInternationalSydney-ATPSydney2014  ATP   
5896  5462451 2014-01-08           ApiaInternationalSydney-ATPSydney2014  ATP   
5897  5462448 2014-01-08           ApiaInternationalSydney-ATPSydney2014  ATP   
5898  5458659 2014-01-08           ApiaInternationalSydney-ATPSydney2014  ATP   
5899  5462447 2014-01-08           ApiaInternationalSydney-ATPSydney2014  ATP   
5900  5462449 2014-01-08           ApiaInternationalSydney-ATPSydney2014  ATP   
5901  5462452 2014-01-08           ApiaInternationalSydney-ATPSydney2014  ATP   
5902  5462453 2014-01-08           ApiaInternationalSydney-ATPSydney2014  ATP   
5903  5466481 2014-01-09           ApiaInternationalSydney-ATPSydney2014  ATP   
5904  5466482 2014-01-09           ApiaInternationalSydney-ATPSydney2014  ATP   
5905  5466483 2014-01-09           ApiaInternationalSydney-ATPSydney2014  ATP   
5906  5466484 2014-01-09           ApiaInternationalSydney-ATPSydney2014  ATP   
5919  5431368 2014-01-01               BrisbaneInternational-ATPBrisbane  ATP   
5920  5431753 2014-01-01               BrisbaneInternational-ATPBrisbane  ATP   
5921  5434811 2014-01-01               BrisbaneInternational-ATPBrisbane  ATP   
5922  5431367 2014-01-01               BrisbaneInternational-ATPBrisbane  ATP   
5923  5434897 2014-01-02               BrisbaneInternational-ATPBrisbane  ATP   
5924  5434813 2014-01-02               BrisbaneInternational-ATPBrisbane  ATP   
5925  5434926 2014-01-02               BrisbaneInternational-ATPBrisbane  ATP   
5926  5442638 2014-01-02               BrisbaneInternational-ATPBrisbane  ATP   
5927  5438543 2014-01-03               BrisbaneInternational-ATPBrisbane  ATP   
5928  5442473 2014-01-03               BrisbaneInternational-ATPBrisbane  ATP   
5929  5442471 2014-01-03               BrisbaneInternational-ATPBrisbane  ATP   
5930  5438544 2014-01-03               BrisbaneInternational-ATPBrisbane  ATP   
5931  5446472 2014-01-04               BrisbaneInternational-ATPBrisbane  ATP   
5932  5446474 2014-01-04               BrisbaneInternational-ATPBrisbane  ATP   
5933  5450726 2014-01-05               BrisbaneInternational-ATPBrisbane  ATP   
5934  5451003 2014-01-06                    HeinekenOpen-ATPAuckland2014  ATP   
5935  5451010 2014-01-06              

In [500]:
# Clean games_2014_to_2015
for index, match in games_2014_to_2015.iterrows():
    player_1 = match["server1"]
    player_2 = match["server2"]
    
    if player_1 not in players_big or player_2 not in players_big:
        games_2014_to_2015.drop(index, inplace=True)

games_2014_to_2015.reset_index(inplace=True)

/Users/VillasBoas/anaconda3/lib/python3.6/site-packages/pandas/core/frame.py:4174: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [507]:
games_2014_to_2015[games_2014_to_2015["tny_name"] == "Men'sUSOpen."]

index   pbp_id       date      tny_name tour  draw  \
1799   7803  6445431 2014-08-27  Men'sUSOpen.  ATP  Main   
1800   7804  6445437 2014-08-27  Men'sUSOpen.  ATP  Main   
1801   7805  6450249 2014-08-27  Men'sUSOpen.  ATP  Main   
1802   7806  6450246 2014-08-27  Men'sUSOpen.  ATP  Main   
1803   7807  6450247 2014-08-27  Men'sUSOpen.  ATP  Main   
1804   7808  6445430 2014-08-27  Men'sUSOpen.  ATP  Main   
1805   7809  6445436 2014-08-27  Men'sUSOpen.  ATP  Main   
1806   7810  6450251 2014-08-27  Men'sUSOpen.  ATP  Main   
1807   7811  6445433 2014-08-27  Men'sUSOpen.  ATP  Main   
1808   7812  6445443 2014-08-27  Men'sUSOpen.  ATP  Main   
1809   7813  6445441 2014-08-27  Men'sUSOpen.  ATP  Main   
1810   7814  6463097 2014-08-27  Men'sUSOpen.  ATP  Main   
1811   7815  6445434 2014-08-27  Men'sUSOpen.  ATP  Main   
1812   7816  6445442 2014-08-28  Men'sUSOpen.  ATP  Main   
1813   7818  6467337 2014-08-28  Men'sUSOpen.  ATP  Main   
1814   7819  6467335 2014-08-28  Men'sUSOpen.  ATP  Main   
1815   7820  6463093 2014-08-28  Men'sUSOpen.  ATP  Main   
1816   7821  6467336 2014-08-28  Men'sUSOpen.  ATP  Main   
1817   7822  6463092 2014-08-28  Men'sUSOpen.  ATP  Main   
1818   7823  6463100 2014-08-28  Men'sUSOpen.  ATP  Main   
1819   7824  6463090 2014-08-28  Men'sUSOpen.  ATP  Main   
1820   7825  6463099 2014-08-28  Men'sUSOpen.  ATP  Main   
1821   7827  6463094 2014-08-28  Men'sUSOpen.  ATP  Main   
1822   7828  6463098 2014-08-28  Men'sUSOpen.  ATP  Main   
1823   7829  6463101 2014-08-28  Men'sUSOpen.  ATP  Main   
1824   7830  6463095 2014-08-29  Men'sUSOpen.  ATP  Main   
1825   7831  6467341 2014-08-29  Men'sUSOpen.  ATP  Main   
1826   7832  6468944 2014-08-29  Men'sUSOpen.  ATP  Main   
1827   7833  6468949 2014-08-29  Men'sUSOpen.  ATP  Main   
1828   7834  6468951 2014-08-29  Men'sUSOpen.  ATP  Main   
1829   7835  6467342 2014-08-29  Men'sUSOpen.  ATP  Main   
1830   7836  6468948 2014-08-29  Men'sUSOpen.  ATP  Main   
1831   7837  6468953 2014-08-29  Men'sUSOpen.  ATP  Main   
1832   7838  6468959 2014-08-29  Men'sUSOpen.  ATP  Main   
1833   7839  6467339 2014-08-29  Men'sUSOpen.  ATP  Main   
1834   7840  6467344 2014-08-29  Men'sUSOpen.  ATP  Main   
1835   7841  6468940 2014-08-29  Men'sUSOpen.  ATP  Main   
1836   7842  6467343 2014-08-29  Men'sUSOpen.  ATP  Main   
1837   7843  6467345 2014-08-29  Men'sUSOpen.  ATP  Main   
1838   7844  6468942 2014-08-29  Men'sUSOpen.  ATP  Main   
1839   7845  6467346 2014-08-29  Men'sUSOpen.  ATP  Main   
1840   7846  6472518 2014-08-30  Men'sUSOpen.  ATP  Main   
1841   7847  6472524 2014-08-30  Men'sUSOpen.  ATP  Main   
1842   7848  6472512 2014-08-30  Men'sUSOpen.  ATP  Main   
1843   7849  6472497 2014-08-30  Men'sUSOpen.  ATP  Main   
1844   7850  6472505 2014-08-30  Men'sUSOpen.  ATP  Main   
1845   7851  6472502 2014-08-30  Men'sUSOpen.  ATP  Main   
1846   7852  6472514 2014-08-31  Men'sUSOpen.  ATP  Main   
1847   7853  6478058 2014-08-31  Men'sUSOpen.  ATP  Main   
1848   7854  6478056 2014-08-31  Men'sUSOpen.  ATP  Main   
1849   7855  6478067 2014-08-31  Men'sUSOpen.  ATP  Main   
1850   7856  6478050 2014-08-31  Men'sUSOpen.  ATP  Main   
1851   7857  6478055 2014-08-31  Men'sUSOpen.  ATP  Main   
1852   7858  6478071 2014-08-31  Men'sUSOpen.  ATP  Main   
1853   7859  6478063 2014-09-01  Men'sUSOpen.  ATP  Main   
1854   7860  6489171 2014-09-01  Men'sUSOpen.  ATP  Main   
1855   7861  6481521 2014-09-01  Men'sUSOpen.  ATP  Main   
1856   7862  6481526 2014-09-01  Men'sUSOpen.  ATP  Main   
1857   7864  6481534 2014-09-02  Men'sUSOpen.  ATP  Main   
1858   7865  6489344 2014-09-02  Men'sUSOpen.  ATP  Main   
1859   7866  6489346 2014-09-02  Men'sUSOpen.  ATP  Main   
1860   7867  6489345 2014-09-02  Men'sUSOpen.  ATP  Main   
1861   7868  6489347 2014-09-03  Men'sUSOpen.  ATP  Main   
1862   7870  6493708 2014-09-04  Men'sUSOpen.  ATP  Main   
1863   7871  6498107 2014-09-04  Men'sUSOpen.  ATP  Main   
1864   7872  6445413 2014-08-25  Men'sUSOpen. 

In [510]:
games_before_2014[games_before_2014["tny_name"] == "Men'sUSOpen"]

index   pbp_id       date     tny_name tour  draw  \
169     169  2306739 2011-08-29  Men'sUSOpen  ATP  Main   
170     170  2311568 2011-08-29  Men'sUSOpen  ATP  Main   
171     171  2311567 2011-08-29  Men'sUSOpen  ATP  Main   
172     172  2306730 2011-08-29  Men'sUSOpen  ATP  Main   
173     173  2306746 2011-08-29  Men'sUSOpen  ATP  Main   
174     174  2306745 2011-08-29  Men'sUSOpen  ATP  Main   
175     175  2311569 2011-08-29  Men'sUSOpen  ATP  Main   
176     176  2311570 2011-08-29  Men'sUSOpen  ATP  Main   
177     177  2306740 2011-08-29  Men'sUSOpen  ATP  Main   
178     178  2306742 2011-08-29  Men'sUSOpen  ATP  Main   
179     179  2306738 2011-08-29  Men'sUSOpen  ATP  Main   
180     180  2306736 2011-08-30  Men'sUSOpen  ATP  Main   
181     181  2306737 2011-08-30  Men'sUSOpen  ATP  Main   
182     182  2306743 2011-08-30  Men'sUSOpen  ATP  Main   
183     183  2306759 2011-08-30  Men'sUSOpen  ATP  Main   
184     184  2306765 2011-08-30  Men'sUSOpen  ATP  Main   
185     185  2311577 2011-08-30  Men'sUSOpen  ATP  Main   
186     186  2306768 2011-08-30  Men'sUSOpen  ATP  Main   
268     268  2340461 2011-09-10  Men'sUSOpen  ATP  Main   
269     269  2344849 2011-09-10  Men'sUSOpen  ATP  Main   
270     270  2347869 2011-09-12  Men'sUSOpen  ATP  Main   
2530   2541  3383369 2012-08-27  Men'sUSOpen  ATP  Main   
2531   2542  3383370 2012-08-27  Men'sUSOpen  ATP  Main   
2532   2543  3390926 2012-08-27  Men'sUSOpen  ATP  Main   
2533   2544  3390927 2012-08-27  Men'sUSOpen  ATP  Main   
2534   2545  3390924 2012-08-27  Men'sUSOpen  ATP  Main   
2535   2546  3383366 2012-08-27  Men'sUSOpen  ATP  Main   
2536   2547  3383354 2012-08-27  Men'sUSOpen  ATP  Main   
2537   2548  3390922 2012-08-27  Men'sUSOpen  ATP  Main   
2538   2549  3383371 2012-08-27  Men'sUSOpen  ATP  Main   
2539   2550  3383360 2012-08-27  Men'sUSOpen  ATP  Main   
2540   2551  3390925 2012-08-27  Men'sUSOpen  ATP  Main   
2541   2552  3383375 2012-08-27  Men'sUSOpen  ATP  Main   
2542   2553  3398883 2012-08-27  Men'sUSOpen  ATP  Main   
2543   2554  3383356 2012-08-27  Men'sUSOpen  ATP  Main   
2544   2555  3390921 2012-08-27  Men'sUSOpen  ATP  Main   
2545   2556  3383355 2012-08-27  Men'sUSOpen  ATP  Main   
2546   2557  3383357 2012-08-27  Men'sUSOpen  ATP  Main   
2547   2558  3383363 2012-08-28  Men'sUSOpen  ATP  Main   
2548   2559  3383373 2012-08-28  Men'sUSOpen  ATP  Main   
2549   2560  3383353 2012-08-28  Men'sUSOpen  ATP  Main   
2550   2561  3383364 2012-08-28  Men'sUSOpen  ATP  Main   
2551   2562  3383358 2012-08-28  Men'sUSOpen  ATP  Main   
2552   2563  3383365 2012-08-28  Men'sUSOpen  ATP  Main   
2553   2564  3383367 2012-08-28  Men'sUSOpen  ATP  Main   
2554   2565  3383372 2012-08-28  Men'sUSOpen  ATP  Main   
2555   2566  3383359 2012-08-28  Men'sUSOpen  ATP  Main   
2556   2567  3383398 2012-08-28  Men'sUSOpen  ATP  Main   
2557   2568  3390928 2012-08-28  Men'sUSOpen  ATP  Main   
2558   2569  3390932 2012-08-28  Men'sUSOpen  ATP  Main   
2559   2570  3383362 2012-08-28  Men'sUSOpen  ATP  Main   
2560   2571  3383399 2012-08-28  Men'sUSOpen  ATP  Main   
2561   2572  3383401 2012-08-28  Men'sUSOpen  ATP  Main   
2562   2573  3383396 2012-08-28  Men'sUSOpen  ATP  Main   
2563   2574  3383395 2012-08-28  Men'sUSOpen  ATP  Main   
2564   2575  3383400 2012-08-28  Men'sUSOpen  ATP  Main   
2565   2576  3390933 2012-08-28  Men'sUSOpen  ATP  Main   
2566   2577  3390934 2012-08-28  Men'sUSOpen  ATP  Main   
2567   2578  3383397 2012-08-28  Men'sUSOpen  ATP  Main   
2568   2579  3383394 2012-08-28  Men'sUSOpen  ATP  Main   
2569   2580  3383402 2012-08-29  Men'sUSOpen  ATP  Main   
2570   2581  3383377 2012-08-29  Men'sUSOpen  ATP  Main   
2571   2582  3383379 2012-08-29  Men'sUSOpen  ATP  Main   
2572   2583  3390931 2012-08-29  Men'sUSOpen  ATP  Main   
2657   2668  3433875 2012-09-08  Men'sUSOpen  ATP  Main   
2658   2669  3441669 2012-09-09  Men'sUSOpen  ATP  Main   
2659   2670  3446055 2012-09-10  Men'sUSOpen  ATP  Ma

In [528]:
w1 = "Men'sAustralianOpenWildCardPlayoff" 
w2 = "Men'sAustralianOpenWildcardPlayoff"

In [534]:
from dateutil.relativedelta import relativedelta
datetime.strptime("03 Feb 14", '%d %b %y') - relativedelta(years=1)

datetime.datetime(2013, 2, 3, 0, 0)